In [1]:
import ast
import csv
import json

import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
from matplotlib_venn import venn2, venn2_circles

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

pd.set_option('display.max_columns', None)

In [19]:
df_09 = pd.read_csv('../data/interim/ds_dedup09.csv', sep=';', quotechar='"', header=None, names=['dedup_id', 'duplicate_id', 'original_id', 'name', 'source'])
df_09.describe()

dedup_id  \
count                                      4513   
unique                                     2145   
top     dedup::75e33da9b103b7b91dcd8da0abe1354b   
freq                                          5   

                               duplicate_id original_id                  name  \
count                                  4513        4513                  4513   
unique                                 4513        4261                  3894   
top     https://fairsharing.org/bsg-d001520        3860  UPN JATIM REPOSITORY   
freq                                      1           2                     4   

       source  
count    4513  
unique      4  
top      roar  
freq     1933

In [13]:
re3data_df = pd.read_csv('../data/raw/re3data.tsv', delimiter='\t', 
                        converters={'subject': ast.literal_eval,
                                    'keyword': ast.literal_eval,
                                    'additional_name': ast.literal_eval,
                                    'repository_id': ast.literal_eval,
                                    'type': ast.literal_eval,
                                    'content_type': ast.literal_eval,
                                    'provider_type': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    })

In [14]:
opendoar_df = pd.read_csv('../data/raw/openDoar.tsv', delimiter='\t',
                         converters={'subject': ast.literal_eval,
                                    'additional_name': ast.literal_eval,
                                    'opendoar_id': ast.literal_eval,
                                    'content_type': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    })

In [15]:
roar_df = pd.read_csv('../data/raw/export_roar_CSV.csv', dtype='str')

In [16]:
fairsharing_df = pd.read_csv('../data/raw/FAIRsharingDBrec_summary20210304.csv', 
                             delimiter='|', header=0,
                             names=['full_name', 'short_name', 'fs_url', 'url', 'countries', 'subjects'])

In [17]:
df_09.head()

dedup_id  \
0  dedup::252773ebafcbbac75238b419d964068e   
1  dedup::860320be12a1c050cd7731794e231bd3   
2  dedup::1aa7a8773e6a7fdacbcedf9999009a38   
3  dedup::4801441f041958afaca324c43c40787b   
4  dedup::2841194266115ac1cc04d19630cde46b   

                                     duplicate_id  \
0             https://fairsharing.org/bsg-d001520   
1  opendoar____::2290a7385ed77cc5592dc2153229f082   
2  opendoar____::191f8f858acda435ae0daf994e2a72c2   
3                                           10453   
4  re3data_____::3afbb2b45a3dd218a5a091ca773cf6c5   

                           original_id  \
0  https://fairsharing.org/bsg-d001520   
1                                 1064   
2                                 8648   
3                                10453   
4                         r3d100011189   

                                                name       source  
0                                 ACTRIS Data Centre  FAIRsharing  
1                 oxford university research archive     OpenDOAR  
2                   digital commons@georgia southern     OpenDOAR  
3                                             MCStor         roar  
4  PRISM: University of Calgary's Digital Repository      re3data

In [44]:
dup = df_09.groupby('dedup_id').aggregate(list)
dup['source_set'] = dup.source.map(set)
dup

duplicate_id  \
dedup_id                                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de                                       [4612, 4649]   
dedup::001e6d882e54c780ce269d3c46997287  [re3data_____::4af9fe2bb93511a5e0f0c39e94d6557...   
dedup::0023a1e3447fdb31836536cc903f1310  [opendoar____::c6f798b844366ccd65d99bc7f31e0e0...   
dedup::003ab6b40af9b488decea7c582d150a2  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::0064f599ed0adb5870a5b3ffe438e485  [16034, opendoar____::d1f157379ea7e51d4a8c07af...   
...                                                                                    ...   
dedup::ff49cc40a8890e6a60f40ff3026d2730  [1333, opendoar____::2bd7f907b7f5b6bbd91822c0c...   
dedup::ff4d70de478038c72282b7e4af1d4260  [opendoar____::95a0810a93a87065bf7b28490817e9e...   
dedup::ff826ce6ee85809389f18a5fafe72366  [opendoar____::62e7f2e090fe150ef8deb4466fdc81b...   
dedup::ffbd6cbb019a1413183c8d08f2929307  [3108, opendoar____::ff7d0f525b3be596a51fb9194...   
dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98  [1126, opendoar____::443cb001c138b2561a0d90720...   

                                                                               original_id  \
dedup_id                                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de                                       [4612, 4649]   
dedup::001e6d882e54c780ce269d3c46997287  [r3d100011306, https://fairsharing.org/10.2550...   
dedup::0023a1e3447fdb31836536cc903f1310                                      [3410, 10013]   
dedup::003ab6b40af9b488decea7c582d150a2  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::0064f599ed0adb5870a5b3ffe438e485                                      [16034, 9647]   
...                                                                                    ...   
dedup::ff49cc40a8890e6a60f40ff3026d2730                                       [1333, 1389]   
dedup::ff4d70de478038c72282b7e4af1d4260                                      [9752, 16367]   
dedup::ff826ce6ee85809389f18a5fafe72366                                       [3601, 2608]   
dedup::ffbd6cbb019a1413183c8d08f2929307                                       [3108, 1912]   
dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98                                        [1126, 648]   

                                                                                      name  \
dedup_id                                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de  [IIT Bombay Institutional Repository, IIT Bomb...   
dedup::001e6d882e54c780ce269d3c46997287  [RESID Database of Protein Modifications, RESI...   
dedup::0023a1e3447fdb31836536cc903f1310  [erucu: electronic repository of the ukrainian...   
dedup::003ab6b40af9b488decea7c582d150a2                                 [Synapse, Synapse]   
dedup::0064f599ed0adb5870a5b3ffe438e485  [Giresun University Institutional Repository, ...   
...                                                                                    ...   
dedup::ff49cc40a8890e6a60f40ff3026d2730                     [UnissResearch, unissresearch]   
dedup::ff4d70de478038c72282b7e4af1d4260  [european xfel publication database, European ...   
dedup::ff826ce6ee85809389f18a5fafe72366  [electronic odessa national economic universit...   
dedup::ffbd6cbb019a1413183c8d08f2929307  [Fotografía Sobre España en el Siglo XIX, foto...   
dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98  [RIT Digital Media Library, rit digital media ...   

                                                         source  \
dedup_id                                                          
dedup::000871c1fc726f0b52dc86a4eeb027de            [roar, roar]   
dedup::001e6d882e54c780ce269d3c46997287  [re3data, FAIRsharing]   
dedup::0023a1e3447fdb31836536cc903f1310        [OpenDOAR, roar]   
dedup::003ab6b40af9b488decea7c582d150a2  [FAIRsharing, re3data]   
dedup::

In [45]:
dup[dup.source_set.str.len() >= 3]

duplicate_id  \
dedup_id                                                                                     
dedup::06138bc5af6023646ede0e1f7c1eac75  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::0b7e684c89e746c67c9761ce2b65479c  [re3data_____::44217da669f17a260c0958a679003a7...   
dedup::0bb4aec1710521c12ee76289d9440817  [re3data_____::eb721a14697a05c477d0ae23830e665...   
dedup::139042a4157a773f209847829d80894d  [756, re3data_____::a95b34b344dc049963c35997fe...   
dedup::13d4bfa0321f86f042b34ec79064b316  [opendoar____::e3844e186e6eb8736e9f53c0c588952...   
...                                                                                    ...   
dedup::eded0708dfe855304a50029fccf1a677  [opendoar____::eccbc87e4b5ce2fe28308fd9f2a7baf...   
dedup::ef46a43afd7c7d67e21f4306bb1364e9  [opendoar____::1f74a54f39b3123ad272ca0a06e7463...   
dedup::f296bb3903d8a84d81c47e6db90764b9  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::f3dc6512e46961c363ea402ff218c8fb  [re3data_____::b2fc675049cbf485d9abbccf5232a31...   
dedup::f9aa64cbb57131939eda048250f2dbae  [re3data_____::063765fa6d6358d62ea2d41dde32d3a...   

                                                                               original_id  \
dedup_id                                                                                     
dedup::06138bc5af6023646ede0e1f7c1eac75  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::0b7e684c89e746c67c9761ce2b65479c  [r3d100010423, 375, https://fairsharing.org/10...   
dedup::0bb4aec1710521c12ee76289d9440817                           [r3d100012596, 650, 349]   
dedup::139042a4157a773f209847829d80894d                    [756, r3d100010690, 1330, 5487]   
dedup::13d4bfa0321f86f042b34ec79064b316                        [9411, 15255, r3d100013135]   
...                                                                                    ...   
dedup::eded0708dfe855304a50029fccf1a677                            [3, r3d100012604, 5509]   
dedup::ef46a43afd7c7d67e21f4306bb1364e9  [5870, https://fairsharing.org/10.25504/FAIRsh...   
dedup::f296bb3903d8a84d81c47e6db90764b9  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::f3dc6512e46961c363ea402ff218c8fb  [r3d100012538, 10171, https://fairsharing.org/...   
dedup::f9aa64cbb57131939eda048250f2dbae  [r3d100012692, https://fairsharing.org/10.2550...   

                                                                                      name  \
dedup_id                                                                                     
dedup::06138bc5af6023646ede0e1f7c1eac75  [Crystallography Open Database, Crystallograph...   
dedup::0b7e684c89e746c67c9761ce2b65479c  [Woods Hole Open Access Server, woods hole ope...   
dedup::0bb4aec1710521c12ee76289d9440817  [Digitale Bibliothek Thüringen, digitale bibli...   
dedup::139042a4157a773f209847829d80894d  [Khazar University Institutional Repository, K...   
dedup::13d4bfa0321f86f042b34ec79064b316                     [fordatis, Fordatis, Fordatis]   
...                                                                                    ...   
dedup::eded0708dfe855304a50029fccf1a677                     [ams acta, AMS Acta, AMS Acta]   
dedup::ef46a43afd7c7d67e21f4306bb1364e9                        [heidata, heiDATA, heiDATA]   
dedup::f296bb3903d8a84d81c47e6db90764b9                        [PubChem, PubChem, pubchem]   
dedup::f3dc6512e46961c363ea402ff218c8fb            [DataverseNO, dataverseno, DataverseNO]   
dedup::f9aa64cbb57131939eda048250f2dbae    [Scholars' Mine, Scholars' Mine, scholars mine]   

                                                                         source  \
dedup_id                                                                          
dedup::06138bc5af6023646ede0e1f7c1eac75  [FAIRsharing, roar, re3data, OpenDOAR]   
dedup::0b7e684c89e746c67c9761ce2b65479c        [re3data, OpenDOAR, FAIRsharing]   
dedup::0bb4aec1710521c12ee76289d9440817               [re3data, OpenDOAR, roa

In [33]:
pd.DataFrame(re3data_df[re3data_df.re3data_id.isin(['r3d100013204', 'r3d100013458', 'r3d100012807', 'r3d100012808', 'r3d100012806', 'r3d100012805'])].institution.to_list())

0  \
0  [Harvard University, Institute for Quantitativ...   
1  [Dataverse Project, [], AAA, [technical], non-...   
2  [Harvard University, Institute for Quantitativ...   
3  [Harvard University, Institute for Quantitativ...   
4  [University of Victoria, [UVic], CAN, [general...   
5  [The University of British Columbia, [], CAN, ...   

                                                   1  \
0  [Ontario Council of University Libraries, [CBU...   
1  [Harvard University, Institute for Quantitave ...   
2  [Ontario Council of University Libraries, [CBU...   
3  [Ontario Council of University Libraries, [CBU...   
4  [University of Victoria, Libraries, [], CAN, [...   
5  [University of British Columbia, Library, [], ...   

                                                   2  \
0  [Scholars Portal Dataverse, [], CAN, [general]...   
1  [Ontario Council of University Libraries, [CBU...   
2  [Scholars Portal Dataverse, [dataverse@scholar...   
3  [Scholars Portal Dataverse, [], CAN, [general]...   
4                                               None   
5                                               None   

                                                   3  \
0  [The Dataverse Project, [], AAA, [technical], ...   
1  [University of Toronto, Libraries, [], CAN, [g...   
2  [The Dataverse Project, [], AAA, [technical], ...   
3  [The Dataverse Project, [], AAA, [technical], ...   
4                                               None   
5                                               None   

                                                   4  
0  [University of Ottawa, Library, [Université d'...  
1                                               None  
2  [University of Windsor, [], CAN, [general], no...  
3  [University of Waterloo, [], CAN, [general], n...  
4                                               None  
5                                               None

In [12]:
roar_df[roar_df.eprintid.isin(['4612', '4649'])]

eprintid rev_number eprint_status userid importid source  \
4167      4612         28       archive   1380      NaN    NaN   
4168      4612        NaN           NaN    NaN      NaN    NaN   
4169      4612        NaN           NaN    NaN      NaN    NaN   
4170      4612        NaN           NaN    NaN      NaN    NaN   
4171      4612        NaN           NaN    NaN      NaN    NaN   
4172      4612        NaN           NaN    NaN      NaN    NaN   
4173      4612        NaN           NaN    NaN      NaN    NaN   
16436     4649          8       archive   1380      NaN    NaN   
16437     4649        NaN           NaN    NaN      NaN    NaN   

                     dir            datestamp              lastmod  \
4167   disk0/00/00/46/12  2012-01-08 03:17:02  2012-04-16 10:53:04   
4168                 NaN                  NaN                  NaN   
4169                 NaN                  NaN                  NaN   
4170                 NaN                  NaN                  NaN   
4171                 NaN                  NaN                  NaN   
4172                 NaN                  NaN                  NaN   
4173                 NaN                  NaN                  NaN   
16436  disk0/00/00/46/49  2012-02-05 13:57:01  2012-04-16 10:39:58   
16437                NaN                  NaN                  NaN   

            status_changed           type succeeds commentary  \
4167   2012-01-08 03:17:02  institutional      NaN        NaN   
4168                   NaN            NaN      NaN        NaN   
4169                   NaN            NaN      NaN        NaN   
4170                   NaN            NaN      NaN        NaN   
4171                   NaN            NaN      NaN        NaN   
4172                   NaN            NaN      NaN        NaN   
4173                   NaN            NaN      NaN        NaN   
16436  2012-02-05 13:57:01  institutional      NaN        NaN   
16437                  NaN            NaN      NaN        NaN   

      metadata_visibility latitude longitude relation_type relation_uri  \
4167                 show      NaN       NaN           NaN          NaN   
4168                  NaN      NaN       NaN           NaN          NaN   
4169                  NaN      NaN       NaN           NaN          NaN   
4170                  NaN      NaN       NaN           NaN          NaN   
4171                  NaN      NaN       NaN           NaN          NaN   
4172                  NaN      NaN       NaN           NaN          NaN   
4173                  NaN      NaN       NaN           NaN          NaN   
16436                show      NaN       NaN           NaN          NaN   
16437                 NaN      NaN       NaN           NaN          NaN   

      item_issues_id item_issues_type item_issues_description  \
4167             NaN              NaN                     NaN   
4168             NaN              NaN                     NaN   
4169             NaN              NaN                     NaN   
4170             NaN              NaN                     NaN   
4171             NaN              NaN                     NaN   
4172             NaN              NaN                     NaN   
4173             NaN              NaN                     NaN   
16436            NaN              NaN                     NaN   
16437            NaN              NaN                     NaN   

      item_issues_timestamp item_issues_status item_issues_reported_by  \
4167                    NaN                NaN                     NaN   
4168                    NaN                NaN                     NaN   
4169                    NaN                NaN                     NaN   
4170                    NaN                NaN                     NaN   
4171                    NaN                NaN                     NaN   
4172                    NaN                NaN                     NaN   
4173                    NaN                NaN                     NaN   

In [13]:
re3data_df[re3data_df.re3data_id == 'r3d100011306']

openaire_id    re3data_id  \
1090  re3data_____::4af9fe2bb93511a5e0f0c39e94d6557f  r3d100011306   

                              repository_name additional_name  \
1090  RESID Database of Protein Modifications              []   

                                    repository_url  \
1090  https://pir.georgetown.edu/resid/resid.shtml   

                                          repository_id  \
1090  [FAIRsharing_doi:10.25504/FAIRsharing.qaszjp, ...   

                                            description            type size  \
1090  The RESID Database of Protein Modifications is...  [disciplinary]  NaN   

     update_date start_date end_date  \
1090         NaN       2014      NaN   

                                                subject mission_statement  \
1090  [2 Life Sciences, 201 Basic Biological and Med...            false    

                   content_type   provider_type  \
1090  [Images, Structured text]  [dataProvider]   

                                                keyword  \
1090  [genomes, life sciences, proteins, proteomes, ...   

                                            institution policy  \
1090  [[Georgetown University, Medical Center, [GUMC...  true    

     database_access database_license data_access data_license data_upload  \
1090           true            false        true         true        true    

     data_upload_license software versioning    api pid_system  \
1090              false     true         yes  true       true    

     citation_guideline_url aid_system enhanced_publication  \
1090                  true       true                   yes   

     quality_management certificate metadata_standard syndication  \
1090            unknown      false             false       false    

                                                remarks  entry_date  \
1090  RESID is covered by Thomson Reuters Data Citat...  2014-12-05   

     last_update  
1090  2019-01-17